# Домашнее задание  № 5. Матричные разложения/Тематическое моделирование

### Задание № 1 (4 балла)

Попробуйте матричные разложения с 4 классификаторами - SGDClassifier, KNeighborsClassifier,  RandomForest, ExtraTreesClassifier (про него подробнее почитайте в документации, он похож на RF). Используйте и NMF и SVD. Сравните результаты на кросс-валидации и выберите лучшее сочетание.

В итоге у вас должно получиться, как минимум 8 моделей (два разложения на каждый классификатор). Используйте 1 и те же параметры кросс-валидации. Параметры векторизации, параметры K в матричных разложениях, параметры классификаторов могут быть разными между экспериментами.

Можете взять поменьше данных, если все будет обучаться слишком долго (не ставьте параметр K слишком большим в NMF, иначе точно будет слишком долго)

In [1]:
# Импорты

# !pip install razdel

import pandas as pd
import numpy as np
import re

import string
from string import punctuation

import razdel
from razdel import tokenize

import pymorphy2
from pymorphy2 import MorphAnalyzer
morph = MorphAnalyzer()

import warnings
warnings.filterwarnings("ignore")

from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer, TfidfTransformer
from sklearn.pipeline import Pipeline
from sklearn.decomposition import TruncatedSVD, NMF
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, confusion_matrix
from sklearn.model_selection import KFold, StratifiedKFold

In [2]:
data = pd.read_csv('avito_category_classification.csv')
data.head()

category_name                                        description
0              Автомобили            отличное состояние,обслужиание в салоне
1  Детская одежда и обувь  В отличном состоянии. Фирма KIKO. Очень теплый...
2       Предложение услуг  Изготовление ограждений, перил,качелей, турник...
3              Автомобили  Автомобиль в отличном техническом состоянии. О...
4         Бытовая техника  Продается газовая плита "Гефест" (Белоруссия) ...

In [3]:
def normalize(text):
    normalized_text = [word.text.strip(punctuation) for word in tokenize(text)]
    normalized_text = [word.lower() for word in normalized_text if word and len(word) < 20 ]
    normalized_text = [morph.parse(word)[0].normal_form for word in normalized_text]
    return ' '.join(normalized_text)

In [4]:
data['description_norm'] = data['description'].apply(normalize)

In [5]:
def eval_table(X, y, pipeline, N=6):
    final_results = []
    labels = list(set(y))
    
    fold_metrics = pd.DataFrame(index=labels)
    errors = np.zeros((len(labels), len(labels)))
    
    kfold = StratifiedKFold(n_splits=N, shuffle=True, )
    
    for i, (train_index, test_index) in enumerate(kfold.split(X, y)):
        pipeline.fit(X[train_index], y[train_index])
        preds = pipeline.predict(X[test_index])
        
        fold_metrics[f'precision_{i}'] = precision_score(y[test_index], preds, labels=labels, average=None)
        fold_metrics[f'recall_{i}'] = recall_score(y[test_index], preds, labels=labels, average=None)
        fold_metrics[f'f1_{i}'] = f1_score(y[test_index], preds, labels=labels, average=None)
        errors += confusion_matrix(y[test_index], preds, labels=labels, normalize='true')
    
    result = pd.DataFrame(index=labels)
    result['precision'] = fold_metrics[[f'precision_{i}' for i in range(N)]].mean(axis=1).round(2)
    result['precision_std'] = fold_metrics[[f'precision_{i}' for i in range(N)]].std(axis=1).round(2)
    
    result['recall'] = fold_metrics[[f'recall_{i}' for i in range(N)]].mean(axis=1).round(2)
    result['recall_std'] = fold_metrics[[f'recall_{i}' for i in range(N)]].std(axis=1).round(2)
    
    result['f1'] = fold_metrics[[f'f1_{i}' for i in range(N)]].mean(axis=1).round(2)
    result['f1_std'] = fold_metrics[[f'f1_{i}' for i in range(N)]].std(axis=1).round(2)
    
    # добавим одну колонку со средним по всем классам
    result.loc['mean'] = result.mean().round(2)
    
    name = f"{pipeline.steps[-1][0]} {pipeline.steps[-2][0]}"
    final_result = result.mean().round(2)
    
    return final_result

In [6]:
# Табличка для сравнения результатов работы разных классификаторов с разными разложениями
overall_results = pd.DataFrame(columns = ["precision", "precision_std", "recall", "recall_std", "f1", "f1_std"])

### SGDClassifier

In [7]:
from sklearn.linear_model import SGDClassifier

pipeline_svd_sgd = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('svd', TruncatedSVD(500)),
    ('sgd', SGDClassifier(max_iter=1000, tol=1e-3))
])

pipeline_nmf_sgd = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('sgd', SGDClassifier(max_iter=1000, tol=1e-3))
])

overall_results.loc['SDG Classifier + SVD'] = eval_table(data['description_norm'], data['category_name'], pipeline_svd_sgd)
overall_results.loc['SDG Classifier + NMF'] = eval_table(data['description_norm'], data['category_name'], pipeline_nmf_sgd)

### KNeighborsClassifier

In [8]:
from sklearn.neighbors import KNeighborsClassifier

pipeline_svd_k_nbr = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('svd', TruncatedSVD(500)),
    ('k_nbr', KNeighborsClassifier(n_neighbors=3))
])

pipeline_nmf_k_nbr = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('k_nbr', KNeighborsClassifier(n_neighbors=3))
])

overall_results.loc['KNeighbors + SVD'] = eval_table(data['description_norm'], data['category_name'], pipeline_svd_k_nbr)
overall_results.loc['KNeighbors + NMF'] = eval_table(data['description_norm'], data['category_name'], pipeline_nmf_k_nbr)

### RandomForest

In [9]:
from sklearn.ensemble import RandomForestClassifier

pipeline_svd_ran = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('svd', TruncatedSVD(500)),
    ('ran', RandomForestClassifier(max_depth=2, random_state=0))
])

pipeline_nmf_ran = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('ran', RandomForestClassifier(max_depth=2, random_state=0))
])

overall_results.loc['RandomForest + SVD'] = eval_table(data['description_norm'], data['category_name'], pipeline_svd_ran)
overall_results.loc['RandomForest + NMF'] = eval_table(data['description_norm'], data['category_name'], pipeline_nmf_ran)

### ExtraTreesClassifier

In [10]:
from sklearn.ensemble import ExtraTreesClassifier

pipeline_svd_extra = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), ngram_range=(1,2), min_df=5, max_df=0.4)),
    ('svd', TruncatedSVD(500)),
    ('extra', ExtraTreesClassifier(n_estimators=100, random_state=0))
])

pipeline_nmf_extra = Pipeline([
    ('bow', CountVectorizer(tokenizer=lambda x: x.split(), min_df=3, max_df=0.3)),
    ('tfidf', TfidfTransformer()),
    ('decomposition', NMF(100)),
    ('extra', ExtraTreesClassifier(n_estimators=100, random_state=0))
])

overall_results.loc['ExtraTrees + SVD'] = eval_table(data['description_norm'], data['category_name'], pipeline_svd_extra)
overall_results.loc['ExtraTrees + NMF'] = eval_table(data['description_norm'], data['category_name'], pipeline_nmf_extra)

### Результаты

In [11]:
overall_results.sort_values('f1', ascending = False)

precision  precision_std  recall  recall_std    f1  \
SDG Classifier + SVD       0.76           0.06    0.73        0.04  0.74   
ExtraTrees + NMF           0.74           0.04    0.69        0.05  0.71   
KNeighbors + NMF           0.48           0.05    0.46        0.05  0.45   
KNeighbors + SVD           0.50           0.04    0.43        0.04  0.44   
SDG Classifier + NMF       0.63           0.21    0.42        0.15  0.42   
ExtraTrees + SVD           0.67           0.08    0.38        0.04  0.42   
RandomForest + NMF         0.33           0.07    0.27        0.03  0.24   
RandomForest + SVD         0.16           0.01    0.18        0.02  0.15   

                      f1_std  
SDG Classifier + SVD    0.03  
ExtraTrees + NMF        0.04  
KNeighbors + NMF        0.04  
KNeighbors + SVD        0.03  
SDG Classifier + NMF    0.11  
ExtraTrees + SVD        0.05  
RandomForest + NMF      0.04  
RandomForest + SVD      0.02

Самый высокий результат - у sgd классификатора с svd разложением, за ним, с небольшим отрывом - extratreesclassifier с nmf разложением. У random forest самые низкие показатели с обоими разложениями.

### Задание № 2 (6 баллов)

В Gensim тоже можно добавить нграммы и tfidf. Постройте 1 модель без них (как в семинаре) и еще 3 модели (1 с нграммами, 1 с tfidf и 1 с нграммами и с tfidf). Сранивте качество с помощью метрик (перплексия, когерентность) и на глаз. Определите лучшую модель. Для каждой модели выберите 1 самую красивую на ваш взгляд тему.

Используйте данные википедии из семинара. Можете взять поменьше данных, если все обучается долго.

Важное требование - получившиеся модели не должны быть совсем плохими. Если хороших тем не получается, попробуйте настроить гиперпараметры, отфильтровать словарь по-другому. 

Нграммы добавляются вот так (перед созданиеv словаря)

In [12]:
# texts = [text.split() for text in texts]
# ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4) # threshold можно подбирать
# p = gensim.models.phrases.Phraser(ph)
# ngrammed_texts = p[texts] 

# ! не забудьте, что далее вам нужно будет использовать ngrammed_texts

!! В модели с нграммами вначале посмотрите, что получается после преобразования
Если вы выведите несколько первых текстов в ngrammed_texts, то там должно быть что-то такое:

In [13]:
# [text for text in ngrammed_texts[:3]]
# >> [['новостройка',
#   'нижегородский_область', # нграм
#   'новостро́йка',
#   '—',
#   'сельский',
#   'посёлок',
#   'в',
#   'дивеевский_район', # нграм
#   'нижегородский_область', #нграмм
#   'входить',
#   'в',
#   'состав_сатисский', #нграмм
#   'сельсовет',
#   'посёлок',
#   'расположить',
#   'в',
#   '12,5',
#   'километр',
# ....

Если вы не видите нграммов, то попробуйте изменить параметр threshold

Tfidf добавляется вот так (после векторизации и перед обучением lda)

In [14]:
# tfidf = gensim.models.TfidfModel(corpus, id2word=dictionary, )
# corpus = tfidf[corpus]

### Общее для моделей

In [15]:
# Дополнительные импорты

import gensim
import pyLDAvis.gensim_models
pyLDAvis.enable_notebook()

In [16]:
texts = open(r'wiki_data.txt', encoding='utf-8').read().splitlines()[:3000]
texts = ([normalize(text) for text in texts])

In [17]:
def make_dictionary(txt):
    if type(txt[0]) == str:
        txt = [text.split() for text in txt]
        
    dictionary = gensim.corpora.Dictionary((text for text in txt))
    dictionary.filter_extremes(no_above=0.1, no_below=10)
    dictionary.compactify()
    corpus = [dictionary.doc2bow(text) for text in txt]
    return dictionary, corpus

In [19]:
topics_number = 50

def metrics_lda(model, corpus, dictionary, txt, num_topics=topics_number):
    if type(txt[0]) == str:
        txt = [text.split() for text in txt]
        
    perplexity = np.exp2(-model.log_perplexity(corpus[:1000]))
    
    topics = []
    for topic_id, topic in model.show_topics(num_topics=num_topics, formatted=False):
        topic = [word for word, _ in topic]
        topics.append(topic)

    coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                       texts=[text for text in txt], 
                                                       dictionary=dictionary, coherence='c_v')
    coherence = coherence_model_lda.get_coherence()
    dic_metrics = {'perplexity': perplexity, 'coherence': coherence}
    return dic_metrics

In [20]:
final_overview = pd.DataFrame(columns = ['perplexity', 'coherence'])

### Модель без всего (из семинара)

In [21]:
dic_normal, corp_normal = make_dictionary(texts)
lda_normal = gensim.models.LdaModel(corp_normal, topics_number, id2word=dic_normal, passes=5)
final_overview.loc['Модель с семинара'] = metrics_lda(lda_normal, corp_normal, dic_normal, texts)

In [22]:
pyLDAvis.gensim_models.prepare(lda_normal, corp_normal, dic_normal, mds='mmds')

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
20    -0.030392 -0.023879       1        1  8.628611
17     0.023319 -0.068934       2        1  7.310197
39    -0.126542  0.000699       3        1  7.117636
13    -0.250811  0.178034       4        1  5.570523
16     0.085019  0.092032       5        1  5.393270
2     -0.206153  0.288140       6        1  5.319210
49     0.005104  0.049243       7        1  5.117512
24    -0.075647  0.208858       8        1  4.986013
21    -0.142899 -0.168173       9        1  3.956122
1      0.225789  0.007504      10        1  3.063160
12     0.188865  0.373166      11        1  2.975772
8      0.162565  0.280910      12        1  2.775012
37    -0.199742  0.058547      13        1  2.612813
9     -0.293523  0.057341      14        1  2.512452
26     0.373489  0.176179      15        1  2.078903
15     0.038596  0.144319      16        1  1.969169
43    -0.393481  0.039139      17        1  1.653959
5     -0.094603  0.425802      18        1  1.606743
18     0.178479 -0.010701      19        1  1.582186
28     0.260126  0.310679      20        1  1.567774
7     -0.425801 -0.030650      21        1  1.347301
30    -0.261257 -0.155186      22        1  1.283559
27    -0.330365  0.216164      23        1  1.263703
10    -0.344997 -0.226121      24        1  1.161384
38    -0.398204 -0.150057      25        1  1.151850
6      0.341207  0.271138      26        1  1.059027
22     0.308207 -0.136371      27        1  1.046343
45    -0.281404 -0.329326      28        1  1.007052
35     0.231105 -0.203797      29        1  0.983293
19    -0.306434 -0.096367      30        1  0.971913
48     0.093491 -0.336789      31        1  0.926303
0      0.128006 -0.189985      32        1  0.914999
14    -0.404169  0.181304      33        1  0.870079
41     0.393912  0.014082      34        1  0.827406
11     0.422761 -0.182888      35        1  0.802795
44     0.466126 -0.026662      36        1  0.784257
40     0.344670  0.095229      37        1  0.769346
31     0.151493 -0.392802      38        1  0.606326
36    -0.199248 -0.360102      39        1  0.520979
23     0.035315 -0.479633      40        1  0.495785
34    -0.296352  0.363196      41        1  0.458700
29     0.013293  0.303775      42        1  0.431417
42     0.206315 -0.308528      43        1  0.421730
46    -0.115022 -0.410349      44        1  0.380571
32     0.210388  0.181887      45        1  0.352838
3      0.037660  0.355667      46        1  0.350171
25     0.009371  0.438599      47        1  0.289997
4     -0.081271 -0.298603      48        1  0.257353
47     0.007352 -0.244288      49        1  0.241951
33     0.316287 -0.281440      50        1  0.224531, topic_info=        Term        Freq       Total Category  logprob  loglift
728     день  623.000000  623.000000  Default  30.0000  30.0000
640     уезд  607.000000  607.000000  Default  29.0000  29.0000
100    фильм  571.000000  571.000000  Default  28.0000  28.0000
65      река  567.000000  567.000000  Default  27.0000  27.0000
1890    ссср  581.000000  581.000000  Default  26.0000  26.0000
...      ...         ...         ...      ...      ...      ...
27    дорога    9.506843  430.988649  Topic50  -4.3840   2.2848
40        км    7.737003  543.105925  Topic50  -4.5900   1.8476
2730    2004    5.506761  158.137708  Topic50  -4.9300   2.7414
477    пункт    6.025433  264.753072  Topic50  -4.8400   2.3161
65      река    6.287287  567.782342  Topic50  -4.7975   1.5957

[2682 rows x 6 columns], token_table=      Topic      Freq Term
term                      
644       4  0.785258    0
644      26  0.081798    0
644      35  0.016360    0
644      48  0.098157    0
3770      3  0.071376   00
...     ...       ...  ...
487      23  0.002358    №
487      24  0.002358    №
487      26  0.002358    №
487      37  0.009431    №
487      48  0.002358    №

[16116 rows x 3 columns], R=30, lambda_step

### Модель с n-grams

In [23]:
texts_ngrams = [text.split() for text in texts]
ph = gensim.models.Phrases(texts_ngrams, scoring='npmi', threshold=0.4) # threshold можно подбирать
p = gensim.models.phrases.Phraser(ph)
ngrammed_texts = p[texts_ngrams] 

dic_ngrams, corp_ngrams = make_dictionary(ngrammed_texts)
lda_ngrams = gensim.models.LdaModel(corp_ngrams, topics_number, id2word=dic_ngrams, passes=5)
final_overview.loc['Модель с н-граммами'] = metrics_lda(lda_ngrams, corp_ngrams, dic_ngrams, ngrammed_texts)
# pyLDAvis.gensim_models.prepare(lda_ngrams, corp_ngrams, dic_ngrams, mds='mmds')

In [24]:
pyLDAvis.gensim_models.prepare(lda_ngrams, corp_ngrams, dic_ngrams, mds='mmds')

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
36    -0.022358 -0.092901       1        1  7.367768
0     -0.128419  0.036622       2        1  5.545450
14    -0.189301 -0.016146       3        1  5.424188
28    -0.307766 -0.126597       4        1  5.054502
48     0.059882 -0.004265       5        1  4.958949
40     0.122706  0.048174       6        1  4.957962
17    -0.162716 -0.088720       7        1  4.428570
15     0.390513 -0.004193       8        1  3.589707
46     0.164164 -0.039939       9        1  3.217728
9      0.215709  0.121561      10        1  3.197184
44    -0.016419  0.253499      11        1  3.174265
38    -0.076413 -0.033737      12        1  3.172536
4     -0.085327  0.221890      13        1  2.923370
2     -0.102430  0.115825      14        1  2.900584
25     0.291194 -0.045209      15        1  2.597223
10    -0.159396 -0.263808      16        1  2.596584
49    -0.364468 -0.198164      17        1  2.227436
22     0.250131  0.245321      18        1  2.202496
37    -0.209507  0.236391      19        1  1.955799
32     0.105896 -0.233677      20        1  1.921017
5      0.175659 -0.153425      21        1  1.873243
21     0.179921  0.367271      22        1  1.823248
16     0.082405  0.453650      23        1  1.817905
31    -0.324264  0.088749      24        1  1.743872
29     0.077236  0.152336      25        1  1.531605
19     0.086448  0.347399      26        1  1.358049
34    -0.384897 -0.025361      27        1  1.091572
42    -0.274690  0.419142      28        1  1.069697
26     0.388574  0.176867      29        1  1.056929
20    -0.044971 -0.334472      30        1  1.042886
27    -0.020759 -0.216874      31        1  1.032108
3      0.184135  0.210257      32        1  1.022654
8      0.317296  0.250432      33        1  1.002394
43    -0.240397  0.175880      34        1  0.915182
30     0.342136 -0.354248      35        1  0.891776
1      0.088478 -0.374434      36        1  0.776365
35    -0.344766 -0.290827      37        1  0.719635
24     0.387962 -0.203362      38        1  0.689113
13    -0.056312  0.403421      39        1  0.593379
39     0.181889 -0.392964      40        1  0.586674
11    -0.398462  0.080638      41        1  0.518513
7     -0.006550 -0.452831      42        1  0.505499
12     0.382814  0.071567      43        1  0.488450
23    -0.369928  0.227713      44        1  0.487228
6      0.274047 -0.266697      45        1  0.455573
18    -0.146296 -0.395837      46        1  0.391345
33    -0.179572  0.417029      47        1  0.307686
47     0.472419 -0.097830      48        1  0.307353
45    -0.224962 -0.324128      49        1  0.271824
41    -0.380269 -0.090987      50        1  0.214922, topic_info=           Term        Freq       Total Category  logprob  loglift
1226       село  713.000000  713.000000  Default  30.0000  30.0000
628        уезд  433.000000  433.000000  Default  29.0000  29.0000
3858      хутор  303.000000  303.000000  Default  28.0000  28.0000
2002      улица  346.000000  346.000000  Default  27.0000  27.0000
1931       ссср  408.000000  408.000000  Default  26.0000  26.0000
...         ...         ...         ...      ...      ...      ...
469     станция    6.134334  218.380631  Topic50  -4.6976   2.5703
370       текст    4.319291   87.313534  Topic50  -5.0484   3.1362
1694  известный    5.765046  358.930885  Topic50  -4.7597   2.0113
592      объект    4.249426  143.802179  Topic50  -5.0647   2.6210
106      список    4.257259  187.363181  Topic50  -5.0628   2.3582

[2810 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
0         7  0.189496     1,2
0         9  0.663235     1,2
1         6  0.065910  1,5_км
1         9  0.131821  1,5_км
1        22  0.065910  1,5_км
...     ...       ...     ...
472      34  0.002862       №
472      37  0.002862       №
472      43  0.002862       №
472      44  0.034342       №

### Модель с tf-idf

In [25]:
tfidf = gensim.models.TfidfModel(corp_normal, id2word=dic_normal)
corp_tfidf = tfidf[corp_normal]
lda_tfidf = gensim.models.LdaModel(corp_tfidf, topics_number, id2word=dic_normal, passes=5)
final_overview.loc['Модель с tf-idf'] = metrics_lda(lda_tfidf, corp_tfidf, dic_normal, texts)


In [26]:
pyLDAvis.gensim_models.prepare(lda_tfidf, corp_tfidf, dic_normal, mds='mmds')

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
16    -0.341033  0.261657       1        1  20.971647
2     -0.102809 -0.412845       2        1  13.220098
10    -0.323997 -0.256174       3        1   9.301180
46     0.386924  0.013864       4        1   4.574810
23     0.026434  0.368735       5        1   4.338106
27     0.343715 -0.176369       6        1   3.862670
28     0.201212 -0.242346       7        1   2.257533
39    -0.301268  0.103107       8        1   2.078725
48    -0.219630 -0.178764       9        1   1.972204
15     0.103722  0.280134      10        1   1.930485
8      0.186628  0.232150      11        1   1.835124
42    -0.181039  0.227310      12        1   1.791506
9     -0.084287  0.263033      13        1   1.575049
34     0.108342 -0.240703      14        1   1.532199
25     0.260201  0.143905      15        1   1.507914
4     -0.123889 -0.205401      16        1   1.504370
19     0.024010 -0.248908      17        1   1.486857
20    -0.254793 -0.011971      18        1   1.295954
13    -0.264573 -0.093341      19        1   1.241208
41    -0.211088  0.093778      20        1   1.239768
24     0.178603 -0.129766      21        1   1.142116
14    -0.010142 -0.187605      22        1   1.135020
11     0.218989 -0.023055      23        1   1.063377
33     0.032199 -0.139496      24        1   0.987886
31    -0.152036 -0.007731      25        1   0.933965
21    -0.012363  0.192141      26        1   0.924748
40     0.159744  0.104715      27        1   0.866618
47     0.110076 -0.095319      28        1   0.832679
12     0.147156  0.037020      29        1   0.821913
5      0.144136 -0.024612      30        1   0.803822
35    -0.082217 -0.146903      31        1   0.766658
3     -0.076640  0.106231      32        1   0.702581
37     0.057724  0.133676      33        1   0.693241
49    -0.089142  0.016223      34        1   0.662255
43    -0.062670 -0.025677      35        1   0.612821
17     0.088613  0.076499      36        1   0.611578
29     0.003363  0.092079      37        1   0.595157
18    -0.046858  0.056700      38        1   0.561254
38     0.067674  0.015432      39        1   0.560583
1      0.037680  0.064214      40        1   0.539163
30    -0.026439  0.059525      41        1   0.530871
6      0.026801 -0.048331      42        1   0.530181
36    -0.014365 -0.019295      43        1   0.518420
32     0.041834 -0.011502      44        1   0.506060
0      0.010382  0.035286      45        1   0.504020
22    -0.018128 -0.048262      46        1   0.490367
44     0.017811 -0.012606      47        1   0.460559
45     0.007986  0.000439      48        1   0.388111
26     0.000052  0.003879      49        1   0.382215
7      0.007392  0.005251      50        1   0.354355, topic_info=               Term       Freq      Total Category  logprob  loglift
5339    романовский  76.000000  76.000000  Default  30.0000  30.0000
2814         летний  40.000000  40.000000  Default  29.0000  29.0000
3055          ленин  26.000000  26.000000  Default  28.0000  28.0000
5143   подсемейство  23.000000  23.000000  Default  27.0000  27.0000
65             река  33.000000  33.000000  Default  26.0000  26.0000
...             ...        ...        ...      ...      ...      ...
3646              m   0.011553   3.832721  Topic50  -8.5229  -0.1618
125            вода   0.011852   9.332635  Topic50  -8.4973  -1.0261
2075  отечественный   0.011832   9.884087  Topic50  -8.4990  -1.0853
58          посёлок   0.011974  22.666074  Topic50  -8.4871  -1.9033
206            дело   0.011652   9.066888  Topic50  -8.5144  -1.0143

[2123 rows x 6 columns], token_table=      Topic      Freq Term
term                      
644      14  0.304748    0
644      18  0.304748    0
1         1  0.458110  1,5
1        33  0.229055  1,5
5122     28  0.692802  1,8
...     ...       ...  ...
406      13  0.180625    ’
4097      3  0.767734    “
4098      3  

### Модель с n-grams и tf-idf

In [27]:
tfidf_ngrams = gensim.models.TfidfModel(corp_ngrams, id2word=dic_ngrams)
corp_tfidf_ngrams = tfidf_ngrams[corp_ngrams]
lda_tfidf_ngrams = gensim.models.LdaModel(corp_tfidf_ngrams, topics_number, id2word=dic_ngrams, passes=5)
final_overview.loc['Модель с н-граммами и tf-idf'] = metrics_lda(lda_tfidf_ngrams, corp_tfidf_ngrams, dic_ngrams, ngrammed_texts)
# pyLDAvis.gensim_models.prepare(lda_tfidf_ngrams, corp_tfidf_ngrams, dic_ngrams,  mds='mmds')

In [28]:
pyLDAvis.gensim_models.prepare(lda_tfidf_ngrams, corp_tfidf_ngrams, dic_ngrams,  mds='mmds')

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
44    -0.342935  0.249390       1        1  17.986384
18    -0.101832 -0.409833       2        1  11.547348
48    -0.319889 -0.268105       3        1  10.499967
5      0.415519  0.027839       4        1   9.506565
17     0.027845  0.370180       5        1   3.846471
25     0.351275 -0.140989       6        1   3.181548
38     0.201196 -0.276887       7        1   2.829914
41    -0.298617  0.085245       8        1   2.653768
43    -0.256684 -0.155316       9        1   2.321624
16     0.129396  0.292358      10        1   2.157107
30     0.225018  0.215077      11        1   2.146809
19    -0.178099  0.197489      12        1   1.883287
27    -0.110549  0.276712      13        1   1.844080
15     0.081303 -0.268991      14        1   1.518741
40     0.245802  0.105795      15        1   1.373381
46    -0.121363 -0.171339      16        1   1.178394
10    -0.000223 -0.199235      17        1   1.173427
11    -0.279235 -0.035529      18        1   1.052150
20    -0.183063 -0.093699      19        1   0.991131
45    -0.140302  0.055674      20        1   0.945845
47     0.166799 -0.088704      21        1   0.919224
28    -0.027784 -0.170375      22        1   0.900577
49     0.177317 -0.043751      23        1   0.886725
12     0.057692 -0.136300      24        1   0.834356
23    -0.138478 -0.004297      25        1   0.812385
29    -0.004511  0.198272      26        1   0.804957
3      0.118373  0.053630      27        1   0.779175
22     0.117077 -0.124813      28        1   0.758352
42     0.102824  0.062345      29        1   0.750624
39     0.137251  0.005039      30        1   0.739665
2     -0.057263 -0.106765      31        1   0.726094
37    -0.087952  0.090719      32        1   0.721174
7      0.061232  0.115627      33        1   0.687440
21    -0.077945  0.018409      34        1   0.653443
8     -0.072826 -0.032779      35        1   0.617042
34     0.066392  0.074335      36        1   0.601448
35    -0.021049  0.133410      37        1   0.601357
31    -0.038131  0.083941      38        1   0.601311
14     0.068451  0.009615      39        1   0.586557
0      0.024171  0.083295      40        1   0.579204
36    -0.017484  0.050178      41        1   0.548937
4      0.030157 -0.060185      42        1   0.547855
26    -0.016063 -0.050755      43        1   0.532678
6      0.057687 -0.020972      44        1   0.520522
13    -0.005535  0.031693      45        1   0.515177
24    -0.007841 -0.022104      46        1   0.470342
33     0.025804 -0.015247      47        1   0.438793
9      0.006943 -0.005309      48        1   0.437805
32    -0.003828  0.004477      49        1   0.396127
1      0.013955  0.011532      50        1   0.392713, topic_info=                   Term       Freq      Total Category  logprob  loglift
1771                 ул  32.000000  32.000000  Default  30.0000  30.0000
5929  романовский_район  27.000000  27.000000  Default  29.0000  29.0000
5920           ул_ленин  29.000000  29.000000  Default  28.0000  28.0000
1226               село  40.000000  40.000000  Default  27.0000  27.0000
5897             1_тело  19.000000  19.000000  Default  26.0000  26.0000
...                 ...        ...        ...      ...      ...      ...
1226               село   0.024881  40.499242  Topic50  -7.9002  -1.8551
1378          чемпионат   0.018116   8.422940  Topic50  -8.2175  -0.6021
1819          выступать   0.018427  13.940103  Topic50  -8.2005  -1.0889
339               сезон   0.015391  16.804205  Topic50  -8.3805  -1.4557
469             станция   0.014194  13.288235  Topic50  -8.4615  -1.3020

[2091 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
633      15  0.640385       0
1        16  0.498814  1,5_км
152      14  0.242333     100
152      29  0.484666     100
2274     26  0.593262     101
...     ...       ...    

### Выводы

In [29]:
final_overview

perplexity  coherence
Модель с семинара             4.331155e+02   0.539213
Модель с н-граммами           5.776609e+02   0.533105
Модель с tf-idf               1.005292e+06   0.468028
Модель с н-граммами и tf-idf  1.369736e+06   0.438603

Из таблицы видно, что самые лучшие результаты показала модель без tfidf и n-грамм - у нее самая высокая coherence и самая низкая perplexity. Интересно, что если брать большее число тем, значительно возрастает coherence у двух моделей с tfidf, но вместе с ней и перплексия :(

In [30]:
# Самая красивая тема для стандартной модели

lda_normal.show_topic(12, topn=10)

[('автомобиль', 0.04288531),
 ('подвеска', 0.03623492),
 ('колесо', 0.019317022),
 ('задний', 0.014946561),
 ('передний', 0.012521005),
 ('поворот', 0.011909179),
 ('поперечный', 0.011501479),
 ('ось', 0.009726624),
 ('дорога', 0.009453859),
 ('модель', 0.008632448)]

In [31]:
# Самая красивая тема для  модели c н-граммами

lda_ngrams.show_topic(3, topn=10)

[('поселение', 0.024101753),
 ('деревня', 0.022921113),
 ('камень', 0.01481435),
 ('на_территория', 0.013132758),
 ('канада', 0.012073489),
 ('замок', 0.01171396),
 ('лесной', 0.010718057),
 ('предприятие', 0.009832497),
 ('парк', 0.009616413),
 ('крепость', 0.009013048)]

In [58]:
# Самая красивая тема для tf-idf модели

lda_tfidf.show_topic(8, topn=10)

[('клуб', 0.023630751),
 ('футбол', 0.02132177),
 ('дивизион', 0.018897476),
 ('испания', 0.017086448),
 ('франция', 0.016581666),
 ('пуэрто-рико', 0.01365464),
 ('футбольный', 0.010124314),
 ('поэт', 0.009830102),
 ('подсемейство', 0.0094077885),
 ('тренер', 0.009294076)]

In [51]:
# Самая красивая тема для tf-idf модели с н-граммами

lda_tfidf_ngrams.show_topic(15, topn=10)

[('посёлок', 0.041243114),
 ('деревня', 0.026496897),
 ('сельсовет', 0.021317191),
 ('дорога', 0.016471425),
 ('совхоз', 0.015139953),
 ('сельский_поселение', 0.015077234),
 ('сибирь', 0.013425014),
 ('сельский', 0.012401712),
 ('муниципальный_образование', 0.010931089),
 ('колхоз', 0.010617322)]